# 버토픽(BERTopic)
- 별도 논문은 없는 모델이지만 github에서 2k이상의 스타를 받았을 만큼 주목받고 있는 토픽 모델
- LDA를 대체할 수 있을 만큼의 기술이라고 확신을 얻었다고 주장

- BERT embddings과 클래스 기반(class-based) TF-IDF를 활용하여 주제 설명에 중요한 단어를 유지하면서도 쉽게 해설 할 수 있는 조밀한 클러스터를 만드는 토픽 모델링 기술

- BERT 알고리즘의 세 가지 과정
    - 텍스트 데이터를 SBERT로 임베딩 : paraphrase-multilingual-MiniLM-L12-v2 (50개 이상의 언어로 학습된 다국어 SBERT)
    - 문서를 군집화 : UMAP을 사용하여 임베딩 차원 줄이고 HDBSCAN기술을 사용해 차원 축소된 임베딩을 클러스터링 해 의미적으로 유사한 문서 클러스터를 생성
    - 토픽 표현을 생성 : 클래스 기반 TF -IDF로 토픽을 추출

In [1]:
#!pip install bertopic[visualization]

     ---------------------------------------- 57.6/57.6 KB 3.0 MB/s eta 0:00:00
     ---------------------------------------- 86.8/86.8 KB 4.8 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'

  error: subprocess-exited-with-error
  
  exit code: 1
  
  [40 lines of output]
  running bdist_wheel
  running build
  running build_py
  creating build
  creating build\lib.win-amd64-3.9
  creating build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\flat.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\hdbscan_.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\plots.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\prediction.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\robust_single_linkage_.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\validity.py -> build\lib.win-amd64-3.9\hdbscan
  copying hdbscan\__init__.py -> build\lib.win-amd64-3.9\hdbscan
  creating build\lib.win-amd64-3.9\hdbscan\tests
  copying hdbscan\tests\test_flat.py -> build\lib.win-amd64-3.9\hdbscan\tests
  copying hdbscan\tests\test_hdbscan.py -> build\lib.win-amd64-3.9\hdbscan\tests
  copying hdbscan\tests\test_prediction_utils.py -> build\lib.win-amd64-3.9\hdbscan\tests
  co


     -------------------------------------- 213.4/213.4 KB 6.3 MB/s eta 0:00:00
     ---------------------------------------- 5.2/5.2 MB 12.3 MB/s eta 0:00:00
  Installing build dependencies: started
  Installing build dependencies: finished with status 'done'
  Getting requirements to build wheel: started
  Getting requirements to build wheel: finished with status 'done'
  Preparing metadata (pyproject.toml): started
  Preparing metadata (pyproject.toml): finished with status 'done'
     ---------------------------------------- 1.1/1.1 MB 12.0 MB/s eta 0:00:00
  Preparing metadata (setup.py): started
  Preparing metadata (setup.py): finished with status 'done'
  Created wheel for umap-learn: filename=umap_learn-0.5.2-py3-none-any.whl size=82708 sha256=4559033790357f8fe75d500443d3631f2c5d79131a9105058c1a66b18b73b0fb
  Stored in directory: c:\users\82104\appdata\local\pip\cache\wheels\4a\66\81\205d77bd58539a1d07fb8b795fcea0b17f4d59912c0f4202b7
  Created wheel for pynndescent: filename=

In [29]:
from tqdm import tqdm
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from bertopic import BERTopic
import pandas as pd
import numpy as np
from konlpy.tag import Okt



In [ ]:
# 파일 불러오기
df = pd.read_parquet('after_preprocessing.parquet')

In [7]:
tour = df['source'].unique()
tour_df = df[df['source']==tour[0]]
tour_df

source                                            content  postdate  \
0    휴애리 자연생활공원  언니 평소 가보고 싶어 하던 휴애리 축제 다녀왔어요 지금 한참 만발 해서 꽃길 걷다...  20211217   
1    휴애리 자연생활공원  안녕하세요 아델라 입니다 이번 포스팅 휴애리 자연생활공원 사진 많은 이었어요 저희 ...  20220227   
2    휴애리 자연생활공원  제주도 휴애리 자연생활공원 제주 매화축제 구경 제주 서귀포시 남원읍 매일 연중 입장...  20220306   
3    휴애리 자연생활공원  안녕하세요 량애 절반 지나가고 있네요 아직도 머물러 있어요 제주도 여행 다녀온지 얼...  20220127   
4    휴애리 자연생활공원  서귀포 가볼만 휴애리 자연생활공원 동백 포토 진짜 제주도 가서 이렇게 동백 미친듯이...  20220104   
..          ...                                                ...       ...   
693  휴애리 자연생활공원  초여름 사실 신록 어울림 느낄 있는 시기 여전히 미세먼지 걱정 앞서긴 공기 맑은 바...  20180529   
694  휴애리 자연생활공원  여행 비수기 하죠 놓치지 말아야 축제 열린다는 마지막 겨울 만끽 있는 얼음 낚시 벌...  20200122   
695  휴애리 자연생활공원  아이 데리 나들이 하기 좋은 가을 맞아 선선 바람 타고 전국 축제 소식 들리네요 예...  20180913   
696  휴애리 자연생활공원  언제 가도 누구 함께 해도 즐거운 제주 여행 제주도 여행 가시는 들이라면 어느 지역...  20180808   
697  휴애리 자연생활공원  새해 골프 여행 인기 계속 됩니다 해외 골프여행 갈만 정말 많지만 국내 혹은 당일치...  20161021   

    platform  
0      naver  
1      naver  
2      naver  
3      naver  
4      naver  
..       ...  
693   brunch  
694   brunch  
695   brunch  
696   brunch  
697   brunch  

[698 rows x 4 columns]

In [9]:
doc = list(tour_df['content'])

doc

['언니 평소 가보고 싶어 하던 휴애리 축제 다녀왔어요 지금 한참 만발 해서 꽃길 걷다 고간 제주 감귤 체험 알차게 즐기고 돌아온 여행 이었습니다 서귀포 남원읍 자리 휴애리 자연생활공원 볼수 있을 유명하답니다 지금 겨울 대표 동백꽃 넓은 부지 활짝 피어 있어 걷는 발길 마다 온통 핑크색 꽃길 걸어 볼수 있고 아기자기 다양한 포토 인생사진 남길수 있는 휴애리 동백 축제 기간 감귤 체험 할수 있는 시기 입니다 휴애리 자연생활공원 제주 서귀포시 남원읍 입장 시간 매일 하절기 입장 마감 입장 마감 휴애리 자연생활공원 주차장 제주특별자치도 서귀포시 남원읍 신례리 휴애리 입장료 성인 단체 단체 단체 유공 경로 우대 도민 자녀 이상 가구 할인 흑돼지 놀자 시간표 하루 흑돼지 공연 볼수 있으니 시간 맞춰 오시 하나 볼거리 있습니다 이건 따로 관람 없고 입장권 포함 입니다 반려견 동반 가능한 미만 소형견 입장 된다고 합니다 입장 하기 위해 선큐알 체크 온도 체크 꼼꼼하게 서서 마치 들어갑니다 시원하게 뿜어내는 분수 작은 연못 시작 해서 위쪽 올라가면 다른 세상 바로 펼쳐질 한라산 배경 동백꽃 함께 감귤 모자 여자 모습 너무도 사랑스럽네요 제주 휴애리 표지 모델 잡지 주인공 될수도 있으니 예쁘게 차려입거나 조금 밝은 입는게 모도 좋습니다 올레길 부터 걸어 볼까 입구 사람 많이 계셨고 연인 삼각대 세워놓고 커플사진 많이 찍는 모습 혼자 셀카 많이 찍는데이 동행 언니 계서 아주 맘껏 찍혀 보았습니다 공원 넓어서 내도 보고 사진 찍어 다니시는게 하나 안놓치고 볼수 있답니다 볼곳 굉장히 많기 때문 그냥 오면 아쉽고 비행기 타고 오는 한번 이맘때 기다려야 하니 실컷 돌아보시 핑크 리가 있었으면 더욱 아름다웠을 글씨 조형물 여기 단체사진 찍음 누가 봐도 제주 있구나 알수 있어 서자랑 사진 찍기 좋더라고요 여성 스럽고 공주 포토 있죠다 축제 즐기느라 조금 한가한 편이 꽃다발 들고 여유 있게 시간 보내 봅니다 걷다 보면 온실 카페 감귤 체험 흑돼지 공연장 먹이 주기 체험 곤충 테마 관등 있는

In [20]:
class CustomTokenizer:
    def __init__(self, tagger, ):
        self.tagger = tagger
    def __call__(self, sent):
        #sent = sent[:1000000]
        word_tokens = self.tagger.pos(sent)
        stop_word = ['있는','있고','있으니','입니다.','이렇게','있을','휴애리']
        result = [w for w,t in word_tokens if  t not in ['Verb'] or w in stop_word]
        return result

custom_tokenizer = CustomTokenizer(Okt())
vectorizer = CountVectorizer(tokenizer=custom_tokenizer, max_features=3000)

In [21]:
model = BERTopic(embedding_model="sentence-transformers/xlm-r-100langs-bert-base-nli-stsb-mean-tokens", \
                 vectorizer_model=vectorizer,
                 nr_topics=50,
                 top_n_words=10,
                 calculate_probabilities=True)

In [22]:
topics, probs = model.fit_transform(doc)

In [23]:
model.visualize_topics()

In [24]:
model.visualize_distribution(probs[0])

In [26]:
model.get_topic(1)

[('휴애리', 0.07182594251336011),
 ('수국', 0.05761093580258411),
 ('제주', 0.04659603824431347),
 ('자연생활공원', 0.04424261968397237),
 ('사진', 0.04157885867873242),
 ('있는', 0.039265957360370564),
 ('축제', 0.036785031358345044),
 ('제주도', 0.03666183755391971),
 ('체험', 0.03542091325204049),
 ('흑돼지', 0.030903921436220835)]

In [28]:
df['source']

0             휴애리 자연생활공원
1             휴애리 자연생활공원
2             휴애리 자연생활공원
3             휴애리 자연생활공원
4             휴애리 자연생활공원
               ...      
361701       1100고지(휴게소)
361702    (주)제주해양레저 투명카약
361703    (주)제주해양레저 투명카약
361704    (주)제주해양레저 투명카약
361705    (주)제주해양레저 투명카약
Name: source, Length: 361706, dtype: object